In [1]:
from app_hawkes import *

In [44]:
def calculate_freq_avg_periodogram_mirrored(x, m, f_minus_j_0=False):
    """
    Calculate the smoothed spectral density estimate using log-window with sinusoidal tapers.

    Parameters:
    x (np.ndarray): time series (num_series, num_series, num_samples).
    m (int): Number of tapers to use.

    Returns:
    w_k (np.ndarray): Sinusoidal taper weights of shape (m,).
    f_hat (np.ndarray): Smoothed spectral density estimate of shape (num_series, num_series, num_frequencies).
    """

    frequences, I = calculate_periodogram(x)
    _, _, num_frequencies = I.shape

    f_hat = np.zeros_like(I, dtype=complex)
    k_values = np.arange(-m // 2, m // 2 + 1)
    w_k = np.cos(np.pi * k_values / m)

    if f_minus_j_0:
        w_k[m // 2] = 0

    # Ensure weights sum to 1
    w_k /= np.sum(w_k)
    
    # Mirror the array
    I_mirrored_left = np.flip(I, axis=-1)  # Mirrored version of I along the last axis
    I_mirrored_right = np.flip(I, axis=-1)  # Mirrored version of I along the last axis
    
    # Concatenate the original and mirrored arrays
    I_extended = np.concatenate((I_mirrored_left, I, I_mirrored_right), axis=-1)
    
    start = num_frequencies-m//2 
    end = num_frequencies+m//2 + 1
    
    for i in range(num_frequencies):     
        f_hat[:, :, i] = np.sum(I_extended[:, :, start+i: end+i] * w_k, axis=2)
        

    return w_k, f_hat, frequences

In [47]:
# Constants
C = 0.617
D = 0.446
m1 = 0
m2 = 1
num_iter = 10
alpha = 0.05
T = 1024

A_list = [np.array([
    [0.5, 0.0, 0.3],
    [0.0, 0.5, -0.3],
    [0.3, -0.3, 0.5]
])]

x = generate_var_process(A_list, T, 1000, seed=None)
x = x - np.mean(x, axis=1, keepdims=True)


# Frequency-averaged periodogram
m_list = [2, 10,50, 100, 200]
freq_avg_estimators = []
freq_avg_estimators_names = []

# Basic periodogram
frequencies, periodogram_sdf = calculate_periodogram(x, taper=None)

for m_i in m_list:
    print(f"{m_i}")
    freq_avg_estimators_names.append(f'Freq old m={m_i}')
    _, freq_avg_periodogram_sdf_i, _ = calculate_freq_avg_periodogram(x, m_i)
    freq_avg_estimators.append(freq_avg_periodogram_sdf_i)  
    
    freq_avg_estimators_names.append(f'Freq new m={m_i}')
    _, freq_avg_periodogram_sdf_i, _ = calculate_freq_avg_periodogram_mirrored(x, m_i)
    freq_avg_estimators.append(freq_avg_periodogram_sdf_i)
    
plot_sdf_with_theoretical(frequencies, freq_avg_estimators, freq_avg_estimators_names,
                                                     periodogram_sdf, log_scale=False)

2
10
50
100
200


In [49]:
True and not True


False

In [53]:
import numpy as np



def estimate_m_for_5_percent(loaded_config, results_per_m):
    """
    Estimate the value of m that would give exactly 5% zeros in percent_zero_results.

    Parameters:
    loaded_config (dict): The loaded configuration containing m_list.
    results_per_m (dict): Dictionary where keys are values of m and values are lists of results.

    Returns:
    float: The estimated value of m that would give exactly 5% zeros.
    """
    m_list = loaded_config['m_list']
    percent_zero_results = [(np.array(results[0]) != 0).mean() * 100 for m, results in results_per_m.items()]
    
    # Convert to numpy arrays for easier manipulation
    m_array = np.array(m_list)
    percent_zero_array = np.array(percent_zero_results)

    
    # Find the points for interpolation
    if np.any(percent_zero_array == 5):
        # If there's an exact 5% value, return the corresponding m
        return m_array[percent_zero_array == 5][0]
    
    # Ensure the values are sorted for interpolation
    sorted_indices = np.argsort(percent_zero_array)
    m_array = m_array[sorted_indices]
    percent_zero_array = percent_zero_array[sorted_indices]
    
    # Find the closest points around 5% for linear interpolation
    for i in range(len(percent_zero_array) - 1):
        if percent_zero_array[i] < 5 < percent_zero_array[i + 1]:
            x1, y1 = m_array[i], percent_zero_array[i]
            x2, y2 = m_array[i + 1], percent_zero_array[i + 1]
            break
    else:
        raise ValueError("5% is outside the range of the percent_zero_results values.")
    
    # Perform linear interpolation
    estimated_m = x1 + (5 - y1) * (x2 - x1) / (y2 - y1)
    
    return estimated_m

# Example usage
loaded_config = {
    "m_list": [10, 20, 50, 100, 200]
}

results_per_m = {
    10: [[1, 0, 0, 0, 1, 1, 1, 1, 0, 0]],
    20: [[1, 1, 0, 0, 0, 1, 1, 1, 0, 1]],
    50: [[1, 1, 1, 1, 0, 1, 1, 1, 1, 1]],
    100: [[0, 0, 0, 0, 0, 0, 0, 0, 0, 0]],
    200: [[0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]
}

estimated_m = estimate_m_for_5_percent(loaded_config, results_per_m)
print(f"Estimated m for 5% zeros: {estimated_m}")

Estimated m for 5% zeros: 35.0


In [64]:
initial_A_list = [np.array([
    [0.3, 0.0, 0.0, -0.5, 0.2],
    [0.0, 0.3, 0.2, 0.2, 0.5],
    [0.0, 0.0, 0.3, -0.2, 0.2],
    [0.0, 0.0, 0.0, 0.3, 0.0],
    [0.0, 0.0, 0.0, 0.0, 0.3]
])]


x = generate_var_process(initial_A_list, 1024, burn_in=100, seed=None)
x = x - np.mean(x, axis=1, keepdims=True)

plot_time_series(x)



In [59]:
is_var_process_stationary(initial_A_list)

Companion matrix: 
[[-0.3 -0.5 -0.   0.5 -0.2]
 [-0.5 -0.3 -0.2 -0.2 -0.5]
 [-0.  -0.  -0.3  0.2 -0.2]
 [-0.  -0.  -0.  -0.3 -0.2]
 [-0.  -0.  -0.  -0.  -0.3]]
eigenvalues
[ 0.2 -0.8 -0.3 -0.3 -0.3]


np.True_

In [69]:
import numpy as np
from scipy.integrate import quad, tplquad

def u_function(x, m):
    return np.cos(np.pi * x )

def compute_C_u(m):
    # Define the integral of u(x)
    integral_u = quad(lambda x: u_function(x, m), -0.5, 0.5)[0]
    integral_u_squared = quad(lambda x: u_function(x, m)**2, -0.5, 0.5)[0]

    # Compute C_u
    C_u = 0.5 * (integral_u**-2) * integral_u_squared
    return C_u

def compute_D_u(m):
    # Define the integral of u(x)
    integral_u = quad(lambda x: u_function(x, m), -0.5, 0.5)[0]

    # Define the function to be integrated for D_u
    def integrand(z, y, x, m):
        return u_function(x, m) * u_function(y, m) * u_function(x + z, m) * u_function(y + z, m)

    # Compute D_u using tplquad
    integral_D_u = tplquad(
        lambda z, y, x: integrand(z, y, x, m),
        0, 1,  # limits for z
         -0.5, 0.5,  # limits for y
         -0.5, 0.5  # limits for x
    )[0]
    
    D_u = (integral_u**-4) * integral_D_u
    return D_u

# Example usage
m = 20  # Example value of m
C_u = compute_C_u(m)
D_u = compute_D_u(m)

print(f"C_u for m={m}: {C_u}")
print(f"D_u for m={m}: {D_u}")

C_u for m=20: 0.6168502750680849
D_u for m=20: 0.7610085237031439
